In [1]:
!pip install ftfy regex tqdm transformers
!pip install git+https://github.com/openai/CLIP.git

  Cloning https://github.com/openai/CLIP.git to c:\users\user\appdata\local\temp\pip-req-build-6nerfk53
  Resolved https://github.com/openai/CLIP.git to commit dcba3cb2e2827b402d2701e7e1c7d9fed8a20ef1
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Created wheel for clip: filename=clip-1.0-py3-none-any.whl size=1369633 sha256=75845d170ca2950d85879535e61dac6b1e22a94866627c0b835123b58e0ed530
  Stored in directory: C:\Users\User\AppData\Local\Temp\pip-ephem-wheel-cache-faqsojwz\wheels\3f\7c\a4\9b490845988bf7a4db33674d52f709f088f64392063872eb9a
Successfully built clip


  Running command git clone --filter=blob:none --quiet https://github.com/openai/CLIP.git 'C:\Users\User\AppData\Local\Temp\pip-req-build-6nerfk53'
  DEPRECATION: Building 'clip' using the legacy setup.py bdist_wheel mechanism, which will be removed in a future version. pip 25.3 will enforce this behaviour change. A possible replacement is to use the standardized build interface by setting the `--use-pep517` option, (possibly combined with `--no-build-isolation`), or adding a `pyproject.toml` file to the source tree of 'clip'. Discussion can be found at https://github.com/pypa/pip/issues/6334


In [14]:
import clip
import torch
from PIL import Image,UnidentifiedImageError
from tqdm import tqdm
import pandas as pd
import os

In [15]:
device = "cuda" if torch.cuda.is_available() else "cpu"
model,preprocess = clip.load("ViT-B/32", device =device)

fusion_df =pd.read_csv("d:/multiagent-disaster-reasoning/data/fusion.csv")
image_root = "d:/multiagent-disaster-reasoning/data/CrisisMMD_v2.0/data_image"
classes = ["a disaster scene", "a cartoon", "a selfie", "a meme", "a news screenshot"]
text_tokens = clip.tokenize(classes).to(device)
kept_rows=[]
for idx,row in tqdm(fusion_df.iterrows(), total =len(fusion_df)):
    try:
        img_path = os.path.join(image_root,row['image_name'])
        if not os.path.exists(img_path):
            print(f"[{idx}] Image not found : {img_path}")
            continue
        image= preprocess(Image.open(img_path)).unsqueeze(0).to(device)

        with torch.no_grad():
            image_features = model.encode_image(image)
            text_features = model.encode_text(text_tokens)

        logits_per_image = (image_features @ text_features.T).softmax(dim=-1)
        probs =logits_per_image[0].cpu().numpy()
        top_class =classes[probs.argmax()]
        print(f"[{idx}] Top class: {top_class}")

        if top_class == "a disaster scene":
            kept_rows.append(row)

    except UnidentifiedImageError:
        print(f"[{idx}] unreadable image : {image_path}")
        continue
    except Exception as e:
        print(f"[{idx}] Error: {e}")
        continue

cleaned_df = pd.DataFrame(kept_rows)
cleaned_df.to_csv("fusion_cleaned.csv" ,index =False)
print("Saved cleaned_fusion.csv with shape:", cleaned_df.shape)

  0%|                                                                                                                | 1/9301 [00:00<2:22:14,  1.09it/s]

[0] Top class: a disaster scene


  0%|                                                                                                                | 2/9301 [00:01<2:04:20,  1.25it/s]

[1] Top class: a disaster scene


  0%|                                                                                                                | 3/9301 [00:02<1:51:39,  1.39it/s]

...

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 9300/9301 [1:13:30<00:00,  1.33it/s]

[9299] Top class: a disaster scene


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████| 9301/9301 [1:13:31<00:00,  2.11it/s]

[9300] Top class: a disaster scene


Saved cleaned_fusion.csv with shape: (8534, 24)


In [16]:
data= pd.read_csv('d:/multiagent-disaster-reasoning/data/fusion_cleaned.csv')
print(data['disaster_type'].value_counts())

disaster_type
hurricane_maria         2711
hurricane_harvey        2095
hurricane_irma          1944
california_wildfires     942
iraq_iran_earthquake     550
srilanka_floods          292
Name: count, dtype: int64
